In [ ]:
import pandas as pd # type: ignore
from sentence_transformers import SentenceTransformer # type: ignore
from qdrant_client import QdrantClient # type: ignore
from qdrant_client.http import models # type: ignore
import numpy as np # type: ignore
import torch # type: ignore

c:\Users\ACER\Documents\Personal_projects\meal_planner\meal_venv\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
# Check if GPU is available
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print(f"Using device: {device}")

# Initialize the embedding model on GPU
model = SentenceTransformer('all-MiniLM-L6-v2')
model.to(device)

Using device: cuda


c:\Users\ACER\anaconda3\Lib\site-packages\transformers\tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


SentenceTransformer(
  (0): Transformer({'max_seq_length': 256, 'do_lower_case': False}) with Transformer model: BertModel 
  (1): Pooling({'word_embedding_dimension': 384, 'pooling_mode_cls_token': False, 'pooling_mode_mean_tokens': True, 'pooling_mode_max_tokens': False, 'pooling_mode_mean_sqrt_len_tokens': False, 'pooling_mode_weightedmean_tokens': False, 'pooling_mode_lasttoken': False, 'include_prompt': True})
  (2): Normalize()
)

In [ ]:
# Connect to Qdrant
client = QdrantClient(
    url= "",  # Replace with your Qdrant instance URL
    api_key= ""  # Replace with your API key
)

# Load CSV file
df = pd.read_csv('1M_recipes.csv')  # Replace with your CSV file path

# Specify your text columns
text_columns = ['title', 'ingredients', 'directions']  # Replace with your column names

# Create a new collection
collection_name = "recipe_data"  # Choose any name you want
vector_size = 384  # all-MiniLM-L6-v2 produces 384-dimensional vectors

# Create collection
client.recreate_collection(
    collection_name=collection_name,
    vectors_config=models.VectorParams(
        size=vector_size,
        distance=models.Distance.COSINE
    )
)

# Batch size for processing
# For 6GB VRAM, we'll use smaller batches since we're processing 3 columns
main_batch_size = 64  # Main batch size for dataframe processing
encoding_batch_size = 32  # Batch size for encoding

C:\Users\ACER\AppData\Local\Temp\ipykernel_16668\847938598.py:18: DeprecationWarning: `recreate_collection` method is deprecated and will be removed in the future. Use `collection_exists` to check collection existence and `create_collection` instead.
  client.recreate_collection(


In [4]:
# Process and upload data in batches
for i in range(0, len(df), main_batch_size):
    batch_df = df.iloc[i:i+main_batch_size]
    
    # Dictionary to store embeddings for each column
    batch_embeddings = {}
    
    # Generate embeddings for each text column
    for column in text_columns:
        texts = batch_df[column].fillna('').tolist()  # Handle NaN values
        embeddings = model.encode(
            texts,
            show_progress_bar=True,
            batch_size=encoding_batch_size,
            device=device # type: ignore
        )
        batch_embeddings[column] = embeddings
    
    # Clear CUDA cache after generating embeddings
    if torch.cuda.is_available():
        torch.cuda.empty_cache()
    
    # Prepare points for upload
    points = []
    for j in range(len(batch_df)):
        # Create payload with all text columns
        payload = {
            column: batch_df[column].iloc[j] for column in text_columns
        }
        
        # Add embeddings for each text column with unique IDs
        for k, column in enumerate(text_columns):
            point_id = (i + j) * len(text_columns) + k  # Unique ID for each embedding
            vector = batch_embeddings[column][j].tolist()
            
            points.append(
                models.PointStruct(
                    id=point_id,
                    vector=vector,
                    payload={
                        'source_column': column,
                        'text': batch_df[column].iloc[j],
                        **payload  # Include all texts in payload for reference
                    }
                )
            )
    
    # Upload batch to Qdrant
    client.upsert(
        collection_name=collection_name,
        points=points
    )
    
    print(f"Uploaded batch {i//main_batch_size + 1}")

print("Upload completed!")

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

c:\Users\ACER\anaconda3\Lib\site-packages\transformers\models\bert\modeling_bert.py:439: UserWarning: 1Torch was not compiled with flash attention. (Triggered internally at C:\actions-runner\_work\pytorch\pytorch\builder\windows\pytorch\aten\src\ATen\native\transformers\cuda\sdp_utils.cpp:555.)
  attn_output = torch.nn.functional.scaled_dot_product_attention(


Batches:   0%|          | 0/2 [00:00<?, ?it/s]

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

Uploaded batch 1


...

Uploaded batch 3693


Batches:   0%|          | 0/2 [00:00<?, ?it/s]

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

ResponseHandlingException: The read operation timed out

In [ ]:
del model  # This deletes the model and frees up memory

# Clear the GPU cache
torch.cuda.empty_cache()

# Optionally, you can check the current GPU memory usage to confirm if it has been cleared
print(torch.cuda.memory_summary())